In [32]:
import json, requests

import folium
import pandas
import numpy as np

In [3]:
departements_geojson = json.load(open("./departements.geojson"))

In [17]:
departements_geojson["features"][0]["properties"]

{'code': '01', 'nom': 'Ain'}

# Compter le nombre de lettre par département

## Import des données

In [14]:
import pandas 
fichier = pandas.read_csv("departements-francais.csv", sep="	")
fichier

NUMÉRO  \
0                                                    1   
1                                                    2   
2                                                    3   
3                                                    4   
4                                                    5   
..                                                 ...   
98                                                 973   
99                                                 974   
100                                                976   
101                                                NaN   
102  fichier téléchargé depuis le site regions-et-d...   

                         NOM                      REGION        CHEF LIEU  \
0                        Ain        Auvergne-Rhône-Alpes  Bourg-en-Bresse   
1                      Aisne             Hauts-de-France             Laon   
2                     Allier        Auvergne-Rhône-Alpes          Moulins   
3    Alpes-de-Haute-Provence  Provence-Alpes-Côte d'Azur            Digne   
4               Hautes-Alpes  Provence-Alpes-Côte d'Azur              Gap   
..                       ...                         ...              ...   
98                    Guyane                      Guyane          Cayenne   
99                La Réunion                  La Réunion      Saint-Denis   
100                  Mayotte                     Mayotte         Dzaoudzi   
101                      NaN                         NaN              NaN   
102                      NaN                         NaN              NaN   

     SUPERFICIE (km²)  POPULATION  DENSITE (habitants/km2)  
0              5762.0    631877.0                    109.7  
1              7369.0    538659.0                     73.1  
2              7340.0    341613.0                     46.5  
3              6925.0    161799.0                     23.4  
4              5549.0    140916.0                     25.4  
..                ...         ...                      ...  
98            83534.0    259865.0                      3.1  
99             2504.0    850727.0                    339.8  
100             376.0    256518.0                    682.2  
101               NaN         NaN                      NaN  
102               NaN         NaN                      NaN  

[103 rows x 7 columns]

In [15]:
fichier.dtypes

NUMÉRO                      object
NOM                         object
REGION                      object
CHEF LIEU                   object
SUPERFICIE (km²)           float64
POPULATION                 float64
DENSITE (habitants/km2)    float64
dtype: object

## Nétoyage des données (Dom Com etc..)

In [16]:
fichier = fichier.drop(101, axis=0)
fichier = fichier.drop(102, axis=0)
fichier = fichier.drop({96,97,98,99,100}, axis=0)
fichier

NUMÉRO                      NOM                      REGION  \
0       1                      Ain        Auvergne-Rhône-Alpes   
1       2                    Aisne             Hauts-de-France   
2       3                   Allier        Auvergne-Rhône-Alpes   
3       4  Alpes-de-Haute-Provence  Provence-Alpes-Côte d'Azur   
4       5             Hautes-Alpes  Provence-Alpes-Côte d'Azur   
..    ...                      ...                         ...   
91     91                  Essonne               Ile-de-France   
92     92           Hauts-de-Seine               Ile-de-France   
93     93           Seine-St-Denis               Ile-de-France   
94     94             Val-de-Marne               Ile-de-France   
95     95               Val-D'Oise               Ile-de-France   

          CHEF LIEU  SUPERFICIE (km²)  POPULATION  DENSITE (habitants/km2)  
0   Bourg-en-Bresse            5762.0    631877.0                    109.7  
1              Laon            7369.0    538659.0                     73.1  
2           Moulins            7340.0    341613.0                     46.5  
3             Digne            6925.0    161799.0                     23.4  
4               Gap            5549.0    140916.0                     25.4  
..              ...               ...         ...                      ...  
91             Évry            1804.0   1276233.0                    707.3  
92         Nanterre             176.0   1601569.0                   9120.6  
93          Bobigny             236.0   1592663.0                   6742.9  
94          Créteil             245.0   1372389.0                   5601.6  
95         Pontoise            1246.0   1215390.0                    975.5  

[96 rows x 7 columns]

### Création de la liste du nombre de lettres pour chaque département :

In [20]:
nb_depts = []
for element in fichier["NOM"] : 
    nb_depts.append(len(element) - element.count(' ') - element.count('-')) 
    # on ne compte pas les tirets ni les espaces

print(nb_depts)

[3, 5, 6, 20, 11, 14, 7, 8, 6, 4, 4, 7, 14, 8, 6, 8, 16, 4, 7, 10, 10, 8, 12, 6, 8, 5, 5, 4, 10, 9, 4, 12, 4, 7, 7, 13, 5, 12, 5, 4, 6, 10, 5, 10, 15, 6, 3, 12, 6, 12, 6, 5, 10, 7, 16, 5, 8, 7, 6, 4, 4, 4, 11, 9, 19, 14, 18, 7, 8, 5, 10, 12, 6, 6, 11, 5, 13, 12, 8, 10, 5, 4, 13, 3, 8, 6, 6, 11, 6, 5, 19, 7, 12, 12, 10, 9]


### Création de la liste des numéros de département :
On a préalablement regardé où se trouvent 2A et 2B dans le fichier departements_geojson :
Ils sont entre le 06 et le 07.

In [21]:
depts = list(range(96)) # De 0 à 95
for i in range(len(depts)) :
    if i<6 :
        depts[i] = depts[i] + 1
        depts[i] = '0' + str(depts[i]) 
        # Ne pas oublier le zéro devant pour que ça corresponde sur le fichier geojson
        # ET on transforme en chaîne de caractères
    elif i == 6 :
        depts[i] = '2A'
    elif i == 7 :
        depts[i] = '2B'
    elif (i > 7 and i <= 10) :
        depts[i] = depts[i] - 1
        depts[i] = '0' + str(depts[i])
    elif (i > 10 and i < 21) :
        depts[i] = depts[i] - 1
        depts[i] = str(depts[i])
    else :
        depts[i] = str(depts[i])

# on vérifie :
print(depts)

['01', '02', '03', '04', '05', '06', '2A', '2B', '07', '08', '09', '10', '11', '12', '13', '14', '15', '16', '17', '18', '19', '21', '22', '23', '24', '25', '26', '27', '28', '29', '30', '31', '32', '33', '34', '35', '36', '37', '38', '39', '40', '41', '42', '43', '44', '45', '46', '47', '48', '49', '50', '51', '52', '53', '54', '55', '56', '57', '58', '59', '60', '61', '62', '63', '64', '65', '66', '67', '68', '69', '70', '71', '72', '73', '74', '75', '76', '77', '78', '79', '80', '81', '82', '83', '84', '85', '86', '87', '88', '89', '90', '91', '92', '93', '94', '95']


### On crée le dataframe pour la carte

In [22]:
lettres_depts = pandas.DataFrame({'departement': depts, 'nombre': nb_depts})

lettres_depts

departement  nombre
0           01       3
1           02       5
2           03       6
3           04      20
4           05      11
..         ...     ...
91          91       7
92          92      12
93          93      12
94          94      10
95          95       9

[96 rows x 2 columns]

## Génération de la Chroopleth

In [40]:
map_france = folium.Map(location = [46.72756241411763, 2.504892775771885],
               tiles = 'cartodbpositron',
               zoom_start = 6
              )

folium.Choropleth(
    geo_data=departements_geojson,
    name='Nombre de lettres par nom de département',
    data=lettres_depts,
    columns=['departement', 'nombre'], 
    key_on='properties.code', 
    #bins =[3,8,12,16,20],
    fill_color='RdPu',
    legend_name = "nombre de lettres",
    fill_opacity=1,
    line_opacity=0.3,
).add_to(map_france)

map_france

# Arrondissements de Marseille

In [89]:
import time
import requests
import pandas as pd

## On récupère la liste des relations OSM des arrondissements de Marseille

In [90]:
overpass_url = "http://overpass-api.de/api/interpreter"
overpass_query = """
[out:json];
rel(11176261);

out;
"""
response = requests.get(overpass_url, 
                        params={'data': overpass_query})

data = response.json()['elements']
data

relations_arrondissments = []

for arrondissement in data[0]['members']:
    relations_arrondissments.append(arrondissement['ref'])

print(relations_arrondissments)

[76091, 76098, 76105, 76119, 76178, 76190, 76217, 76282, 76337, 76349, 76375, 76382, 76399, 76403, 76409, 76421]


## Fontion pour fetch les Données d'une clef 'content' sur les arrondissments depuis OSM

In [91]:
def fetch_OSM_data(key):

    count = []

    for numero in relations_arrondissments:
        time.sleep(7)
        overpass_query = f'[out:json]; area(36000{str(numero)});( node["{key}"](area); way["{key}"](area); rel["{key}"](area););out center;'

        response = requests.get(overpass_url, 
                                params={'data': overpass_query})

        if response.status_code != 200:
            print(numero, response)
            data=[]
        else:
            print(numero, "ok")
            data = response.json()['elements']
        count.append(len(data))

    return count

### On récupère les données de la clef 'tactile_paving'

In [92]:
tactile_paving = fetch_OSM_data('tactile_paving')

76091 ok
76098 ok
76105 ok
76119 ok
76178 ok
76190 ok
76217 ok
76282 ok
76337 ok
76349 ok
76375 ok
76382 ok
76399 ok
76403 ok
76409 ok
76421 ok


## Fontion pour convertir ces données en pandas.DataFrame

In [93]:
def convert_dataframe(data):
    data = pd.DataFrame({'arrondissement':list(range(13001, 13017)), 
                                            'id':relations_arrondissments, 
                                            'nombre': data})

    # Attention cependant : l'arrondissmeent du geojson est une chaine de caractère. 
    # Il faut donc convertir notre colonne du dataframe d'entier à str.
    data = data.assign(arrondissement=[str(x) for x in data.arrondissement])
    return data

### On converti nos données des pavés tactiles en DataFrame

In [94]:
dataframe_tactile = convert_dataframe(tactile_paving)

## Fonction pour générer la map folium avec les données

In [95]:
def generate_map(dataframe, key):
    arrondissements = json.load(open('./arrondissements.geojson'))

    folium_map = folium.Map(location = [43.2805, 5.3809],
                   tiles = 'cartodbpositron',
                   zoom_start = 11
                  )

    folium.Choropleth(
        geo_data=arrondissements,
        name='choropleth',
        data=dataframe,
        columns=['arrondissement', 'nombre'],
        key_on='properties.arrondissement',
        fill_color='RdPu',
        fill_opacity=0.6,
        line_opacity=0.5,
        legend_name=f'Nombre de {key} par arrondissement'
    ).add_to(folium_map)

    folium.LayerControl().add_to(folium_map)

    return folium_map

### On génére et affiche notre Map de pavés tactiles

In [96]:
tactile_map = generate_map(dataframe_tactile, 'tactile_paving')
display(tactile_map)

## Fonction globale, qui fetch les données depuis OSM et affiche une map folium à partir d'un string qui représente la clef OSM que l'on souhaite étudier.

Map Features OSM : https://wiki.openstreetmap.org/wiki/Map_features

In [97]:
def get_and_display_map(key):
    print(f'Fetchin data for "{key}" key in OSM...')
    OSM_data = fetch_OSM_data(key)
    print('Converting data in pandas.DataFrame...')
    OSM_dataframe = convert_dataframe(OSM_data)
    print('Generation the folium map...')
    folium_map = generate_map(OSM_dataframe, key)
    display(folium_map)

In [98]:
get_and_display_map('historic')

Fetchin data for "historic" key in OSM...
76091 ok
76098 ok
76105 ok
76119 ok
76178 ok
76190 ok
76217 ok
76282 ok
76337 ok
76349 ok
76375 ok
76382 ok
76399 ok
76403 ok
76409 ok
76421 ok
Converting data in pandas.DataFrame...
Generation the folium map...
